In [1]:
import plotly.graph_objects as go
import plotly.express as px
import ipywidgets as widgets
from IPython.display import display, HTML
import pandas as pd

# Visualização e Dashboards
Crie visualizações e dashboards que respondam às seguintes necessidades:
Um dashboard geral que mostre a evolução das vendas ao longo do tempo, com filtros por estado e categoria de produto

# Dashboard Interativo: Evolução das Vendas

Este dashboard permite visualizar a evolução das vendas ao longo do tempo, com filtros dinâmicos por **estado** e **categoria de produto**.  
Utilize os menus suspensos para selecionar o estado e/ou categoria desejada e veja como as vendas mensais variam conforme o filtro aplicado.

**Como usar:**
- Selecione um estado ou "Todos" para visualizar todas as regiões.
- Selecione uma categoria de produto ou "Todas" para visualizar todas as categorias.
- O gráfico será atualizado automaticamente conforme os filtros.

> **Requisitos:**  
> - Execute este bloco em um Jupyter Notebook.  
> - Certifique-se de ter as bibliotecas `plotly` e `ipywidgets` instaladas (`pip install plotly ipywidgets`).

In [2]:
DATA_PATH = "../data/"

files = {
    'customers': 'olist_customers_dataset.csv',
    'geolocation': 'olist_geolocation_dataset.csv',
    'order': 'olist_order_items_dataset.csv',
    'payments': 'olist_order_payments_dataset.csv',
    'reviews': 'olist_order_reviews_dataset.csv',
    'orders': 'olist_orders_dataset.csv',
    'products': 'olist_products_dataset.csv',
    'sellers': 'olist_sellers_dataset.csv',
    'category': 'product_category_name_translation.csv'
}

dfs = {}
for name, file in files.items():
    dfs[name] = pd.read_csv(DATA_PATH + file)

df_dashboard = (
    dfs["orders"]
    .merge(dfs["customers"][["customer_id", "customer_state"]], on="customer_id", how="left")
    .merge(dfs["order"][["order_id", "product_id", "price"]], on="order_id", how="left")
    .merge(dfs["products"][["product_id", "product_category_name"]], on="product_id", how="left")
    .merge(dfs["category"], on="product_category_name", how="left")
)

df_dashboard["order_month"] = pd.to_datetime(df_dashboard["order_purchase_timestamp"]).dt.to_period("M").astype(str)

# Criação da Coluna de Categoria em Português

Este bloco de código cria uma nova coluna chamada `categoria_pt` no DataFrame `df_dashboard`, contendo o nome das categorias de produto em português e formatadas para melhor visualização.  
- Substitui valores nulos por "Não Informado".
- Troca underscores (`_`) por espaços.
- Aplica a capitalização adequada em cada palavra.

Essa coluna facilita a análise e apresentação dos dados em dashboards e relatórios em português.

In [3]:
df_dashboard["categoria_pt"] = df_dashboard["product_category_name"].fillna("Não Informado").str.replace("_", " ").str.title()

# 1) Um dashboard geral que mostre a evolução das vendas ao longo do tempo, com filtros por estado e categoria de produto

Este bloco de código cria um dashboard interativo para análise da evolução das vendas ao longo do tempo, com filtros dinâmicos por **estado** e **categoria de produto**.  
Utiliza as bibliotecas `plotly`, `ipywidgets` e `IPython.display` para criar gráficos interativos e KPIs executivos.

**Funcionalidades:**
- Filtros dropdown para seleção de estado e categoria de produto.
- Gráfico de barras mostrando o valor total das vendas por mês.
- Gráfico de linha mostrando a tendência das vendas mensais.
- KPIs de destaque: vendas totais, média mensal e melhor mês.
- Visual moderno e responsivo, facilitando a análise exploratória.

> **Dica:**  
> Altere os filtros para visualizar rapidamente o desempenho de diferentes regiões e categorias ao longo do tempo.

In [4]:
px.defaults.template = "plotly_white"
px.defaults.color_continuous_scale = "teal"

estado_widget = widgets.Dropdown(
    options=["Todos"] + sorted(df_dashboard["customer_state"].dropna().unique()),
    value="Todos",
    description="Estado:",
    style={"description_width": "initial"},
    layout=widgets.Layout(width="220px")
)
categoria_widget = widgets.Dropdown(
    options=["Todas"] + sorted(df_dashboard["categoria_pt"].dropna().unique()),
    value="Todas",
    description="Categoria:",
    style={"description_width": "initial"},
    layout=widgets.Layout(width="320px")
)

def atualizar_dashboard(estado, categoria):
    df_plot = df_dashboard.copy()
    if estado != "Todos":
        df_plot = df_plot[df_plot["customer_state"] == estado]
    if categoria != "Todas":
        df_plot = df_plot[df_plot["categoria_pt"] == categoria]
    vendas_mes = (
        df_plot.groupby("order_month")["price"]
        .sum()
        .reset_index()
        .sort_values("order_month")
    )
    vendas_mes["price"] = vendas_mes["price"].fillna(0)

    fig = go.Figure()
    fig.add_trace(go.Bar(
        x=vendas_mes["order_month"],
        y=vendas_mes["price"],
        marker_color="#00bfae",
        text=[f"R$ {v:,.0f}".replace(",", ".") for v in vendas_mes["price"]],
        textposition="outside",
        hovertemplate="Mês: %{x}<br>Vendas: R$ %{y:,.2f}<extra></extra>",
        name="Vendas (R$)"
    ))
    fig.add_trace(go.Scatter(
        x=vendas_mes["order_month"],
        y=vendas_mes["price"],
        mode="lines+markers",
        line=dict(color="#ff9800", width=4),
        marker=dict(size=10, color="#ff9800", line=dict(width=2, color="#fff")),
        hovertemplate="Mês: %{x}<br>Vendas: R$ %{y:,.2f}<extra></extra>",
        name="Tendência"
    ))
    fig.update_layout(
        title=f"<b>Evolução das Vendas Mensais</b><br><span style='font-size:16px'>Estado: <b>{estado}</b> | Categoria: <b>{categoria}</b></span>",
        xaxis_title="Mês",
        yaxis_title="Vendas (R$)",
        plot_bgcolor="#f7fafd",
        paper_bgcolor="#f7fafd",
        font=dict(family="Segoe UI", size=15, color="#222"),
        title_font=dict(size=24, color="#00bfae"),
        xaxis_tickangle=-45,
        yaxis_tickprefix="R$ ",
        bargap=0.25,
        height=540,
        legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="right", x=1)
    )
    fig.update_traces(marker_line_color="#00897b", marker_line_width=1.5, selector=dict(type="bar"))
    fig.update_yaxes(showgrid=True, gridcolor="#e0e7ef")

    total_vendas = vendas_mes["price"].sum()
    media_mensal = vendas_mes["price"].mean()
    melhor_mes = vendas_mes.loc[vendas_mes["price"].idxmax(), "order_month"] if not vendas_mes.empty else "-"
    melhor_valor = vendas_mes["price"].max() if not vendas_mes.empty else 0

    display(HTML(f"""
    <div style="display:flex;gap:40px;margin-bottom:10px;">
        <div style="background:#00bfae22;padding:18px 32px;border-radius:12px;box-shadow:0 2px 8px #00bfae22;">
            <div style="font-size:15px;color:#00bfae;">Vendas Totais</div>
            <div style="font-size:2.1em;font-weight:bold;color:#00897b;">R$ {total_vendas:,.0f}</div>
        </div>
        <div style="background:#ff980022;padding:18px 32px;border-radius:12px;box-shadow:0 2px 8px #ff980022;">
            <div style="font-size:15px;color:#ff9800;">Média Mensal</div>
            <div style="font-size:2.1em;font-weight:bold;color:#ff9800;">R$ {media_mensal:,.0f}</div>
        </div>
        <div style="background:#e0e7ef;padding:18px 32px;border-radius:12px;box-shadow:0 2px 8px #e0e7ef;">
            <div style="font-size:15px;color:#222;">Melhor Mês</div>
            <div style="font-size:1.5em;font-weight:bold;color:#222;">{melhor_mes}</div>
            <div style="font-size:1.1em;color:#00897b;">R$ {melhor_valor:,.0f}</div>
        </div>
    </div>
    """))

    fig.show()

display(HTML("""
<h2 style='color:#00bfae;font-size:2em;margin-bottom:0;'>Dashboard Executivo de Vendas</h2>
<p style='font-size:1.1em;margin-top:0;color:#222;'>Explore a evolução das vendas ao longo do tempo.<br>
<b>Use os filtros abaixo</b> para analisar por <b>estado</b> e <b>categoria de produto</b>.</p>
"""))

ui = widgets.HBox([estado_widget, categoria_widget])
out = widgets.interactive_output(
    atualizar_dashboard,
    {"estado": estado_widget, "categoria": categoria_widget}
)

display(ui, out)

Output()

# 2) Um mapa de calor mostrando a concentração de vendas por região/estado do Brasil

In [5]:
df_dashboard["tempo_entrega"] = (
    pd.to_datetime(df_dashboard["order_delivered_customer_date"]) - 
    pd.to_datetime(df_dashboard["order_purchase_timestamp"])
).dt.days

df_avaliacao = (
    df_dashboard[["order_id", "tempo_entrega"]]
    .merge(dfs["reviews"][["order_id", "review_score"]], on="order_id", how="left")
    .dropna(subset=["tempo_entrega", "review_score"])
)

fig_disp = px.scatter(
    df_avaliacao,
    x="tempo_entrega",
    y="review_score",
    color="review_score",
    color_continuous_scale="RdYlGn",
    labels={"tempo_entrega": "Tempo de Entrega (dias)", "review_score": "Avaliação do Cliente"},
    title="Relação entre Avaliação do Cliente e Tempo de Entrega",
    opacity=0.6,
    trendline="ols"
)
fig_disp.update_layout(
    font=dict(family="Segoe UI", size=14),
    plot_bgcolor="#f7fafd",
    paper_bgcolor="#f7fafd"
)
fig_disp.show()

# 3) Um conjunto de gráficos que apresente a relação entre avaliação do cliente e tempo de entrega

In [6]:
df_dashboard["tempo_entrega"] = (
    pd.to_datetime(df_dashboard["order_delivered_customer_date"]) - 
    pd.to_datetime(df_dashboard["order_purchase_timestamp"])
).dt.days

df_avaliacao = (
    df_dashboard[["order_id", "tempo_entrega"]]
    .merge(dfs["reviews"][["order_id", "review_score"]], on="order_id", how="left")
    .dropna(subset=["tempo_entrega", "review_score"])
)

fig_box = px.box(
    df_avaliacao,
    x="review_score",
    y="tempo_entrega",
    color="review_score",
    color_discrete_sequence=px.colors.sequential.Teal,
    labels={"review_score": "Avaliação do Cliente", "tempo_entrega": "Tempo de Entrega (dias)"},
    title="Tempo de Entrega por Nota de Avaliação"
)
fig_box.update_layout(
    font=dict(family="Segoe UI", size=14),
    plot_bgcolor="#f7fafd",
    paper_bgcolor="#f7fafd"
)
fig_box.show()

media_entrega = df_avaliacao.groupby("review_score")["tempo_entrega"].mean().reset_index()
fig_bar = px.bar(
    media_entrega,
    x="review_score",
    y="tempo_entrega",
    color="tempo_entrega",
    color_continuous_scale="teal",
    labels={"review_score": "Avaliação do Cliente", "tempo_entrega": "Tempo Médio de Entrega (dias)"},
    title="Tempo Médio de Entrega por Avaliação"
)
fig_bar.update_layout(
    font=dict(family="Segoe UI", size=14),
    plot_bgcolor="#f7fafd",
    paper_bgcolor="#f7fafd"
)
fig_bar.show()

# 4) Um dashboard de análise dos vendedores, mostrando quais têm melhor desempenho em termos de volume de vendas, satisfação do cliente e tempo de entrega

In [7]:
df_vendedores = (
    df_dashboard
    .merge(dfs["order"][["order_id", "seller_id"]], on="order_id", how="left")
    .merge(dfs["reviews"][["order_id", "review_score"]], on="order_id", how="left")
    .merge(dfs["sellers"][["seller_id", "seller_city", "seller_state"]], on="seller_id", how="left")
    .groupby(["seller_id", "seller_city", "seller_state"])
    .agg(
        vendas_total=("price", "sum"),
        pedidos=("order_id", "nunique"),
        tempo_medio_entrega=("tempo_entrega", "mean"),
        satisfacao_media=("review_score", "mean")
    )
    .reset_index()
)

df_vendedores["vendedor_nome"] = (
    df_vendedores["seller_city"].str.title() + " / " + df_vendedores["seller_state"]
)

criterio_widget = widgets.Dropdown(
    options=[
        ("Volume de Vendas", "vendas_total"),
        ("Satisfação do Cliente", "satisfacao_media"),
        ("Tempo Médio de Entrega", "tempo_medio_entrega")
    ],
    value="vendas_total",
    description="Ordenar por:",
    style={"description_width": "initial"},
    layout=widgets.Layout(width="260px")
)

def atualizar_dashboard_vendedores(criterio):
    df_plot = df_vendedores.copy()
    asc = True if criterio == "tempo_medio_entrega" else False
    df_plot = df_plot.sort_values(criterio, ascending=asc).head(15)

    cor = "teal" if criterio != "tempo_medio_entrega" else "OrRd_r"
    titulos = {
        "vendas_total": "Volume de Vendas",
        "satisfacao_media": "Satisfação do Cliente",
        "tempo_medio_entrega": "Tempo Médio de Entrega"
    }

    fig = px.bar(
        df_plot,
        x="vendedor_nome",
        y=criterio,
        color=criterio,
        color_continuous_scale=cor,
        text_auto=".2s" if criterio == "vendas_total" else ".2f",
        hover_data=["pedidos", "satisfacao_media", "tempo_medio_entrega"],
        labels={
            "vendedor_nome": "Vendedor (Cidade/UF)",
            "vendas_total": "Vendas Totais (R$)",
            "satisfacao_media": "Satisfação Média",
            "tempo_medio_entrega": "Tempo Médio de Entrega (dias)"
        },
        title=f"<b> Top 15 Vendedores por {titulos[criterio]}</b>",
        height=520
    )
    fig.update_layout(
        font=dict(family="Segoe UI", size=15, color="#222"),
        plot_bgcolor="#f7fafd",
        paper_bgcolor="#f7fafd",
        title_font=dict(size=24, color="#00bfae"),
        xaxis_tickangle=-35,
        xaxis_title="Vendedor (Cidade/UF)",
        yaxis_title=None,
        margin=dict(l=40, r=20, t=80, b=80)
    )
    fig.update_traces(
        marker_line_color="#00897b" if criterio != "tempo_medio_entrega" else "#b71c1c",
        marker_line_width=1.5,
        textfont_size=13
    )
    fig.show()

    display(HTML(f"""
    <div style="display:flex;gap:40px;margin-bottom:10px;">
        <div style="background:#00bfae22;padding:14px 28px;border-radius:10px;">
            <div style="font-size:15px;color:#00bfae;">Vendas Totais (Top 15)</div>
            <div style="font-size:1.5em;font-weight:bold;color:#00897b;">R$ {df_plot['vendas_total'].sum():,.0f}</div>
        </div>
        <div style="background:#ff980022;padding:14px 28px;border-radius:10px;">
            <div style="font-size:15px;color:#ff9800;">Satisfação Média (Top 15)</div>
            <div style="font-size:1.5em;font-weight:bold;color:#ff9800;">{df_plot['satisfacao_media'].mean():.2f}</div>
        </div>
        <div style="background:#e0e7ef;padding:14px 28px;border-radius:10px;">
            <div style="font-size:15px;color:#222;">Tempo Médio de Entrega (Top 15)</div>
            <div style="font-size:1.2em;font-weight:bold;color:#222;">{df_plot['tempo_medio_entrega'].mean():.1f} dias</div>
        </div>
    </div>
    """))

display(HTML("""
<h2 style='color:#00bfae;font-size:1.7em;margin-bottom:0;'>Dashboard de Desempenho dos Vendedores</h2>
<p style='font-size:1.1em;margin-top:0;color:#222;'>Veja os vendedores com melhor desempenho em <b>volume de vendas</b>, <b>satisfação do cliente</b> e <b>tempo de entrega</b>.<br>
Altere o critério para comparar diferentes aspectos.</p>
"""))

out_vendedores = widgets.interactive_output(
    atualizar_dashboard_vendedores,
    {"criterio": criterio_widget}
)

display(widgets.HBox([criterio_widget]), out_vendedores)

Output()